In [58]:
import pandas as pd
from sqlalchemy import create_engine
import datetime

# STEP 1: EXTRACT

In [59]:
# DATASOURCE 1: Extract all records from winemag.csv - source kaggle.com

wine_file = "Resources/winemag.csv"
df_wine = pd.read_csv(wine_file)

print("Total records ", df_wine['winery'].count())
df_wine.head()

Total records  129971


Unnamed: 0   country                                        description  \
0           0     Italy  Aromas include tropical fruit, broom, brimston...   
1           1  Portugal  This is ripe and fruity, a wine that is smooth...   
2           2        US  Tart and snappy, the flavors of lime flesh and...   
3           3        US  Pineapple rind, lemon pith and orange blossom ...   
4           4        US  Much like the regular bottling from 2012, this...   

                          designation  points  price           province  \
0                        Vulkà Bianco      87    NaN  Sicily & Sardinia   
1                            Avidagos      87   15.0              Douro   
2                                 NaN      87   14.0             Oregon   
3                Reserve Late Harvest      87   13.0           Michigan   
4  Vintner's Reserve Wild Child Block      87   65.0             Oregon   

              region_1           region_2         taster_name  \
0                 Etna                NaN       Kerin O’Keefe   
1                  NaN                NaN          Roger Voss   
2    Willamette Valley  Willamette Valley        Paul Gregutt   
3  Lake Michigan Shore                NaN  Alexander Peartree   
4    Willamette Valley  Willamette Valley        Paul Gregutt   

  taster_twitter_handle                                              title  \
0          @kerinokeefe                  Nicosia 2013 Vulkà Bianco  (Etna)   
1            @vossroger      Quinta dos Avidagos 2011 Avidagos Red (Douro)   
2           @paulgwine       Rainstorm 2013 Pinot Gris (Willamette Valley)   
3                   NaN  St. Julian 2013 Reserve Late Harvest Riesling ...   
4           @paulgwine   Sweet Cheeks 2012 Vintner's Reserve Wild Child...   

          variety               winery  
0     White Blend              Nicosia  
1  Portuguese Red  Quinta dos Avidagos  
2      Pinot Gris            Rainstorm  
3        Riesling           St. Julian  
4      Pinot Noir         Sweet Cheeks

In [60]:
# Only keep required columns and rename them
wine_cols = ['Unnamed: 0','country','province','region_1','title','variety','winery','points','price']
df_wine_base = df_wine[wine_cols].copy()

df_wine_base = df_wine_base.rename(columns={'Unnamed: 0':'wine_id',
                                            'country': 'country_name',
                                            'province': 'province_name',
                                            'region_1':'region_name',
                                            'title':'wine_name',
                                            'variety':'wine_type',
                                            'winery':'winery_name',
                                            'points':'rating',
                                            'price':'price'})

df_wine_base = df_wine_base.replace(to_replace='US', value='United States')
df_wine_base.head()

wine_id   country_name      province_name          region_name  \
0        0          Italy  Sicily & Sardinia                 Etna   
1        1       Portugal              Douro                  NaN   
2        2  United States             Oregon    Willamette Valley   
3        3  United States           Michigan  Lake Michigan Shore   
4        4  United States             Oregon    Willamette Valley   

                                           wine_name       wine_type  \
0                  Nicosia 2013 Vulkà Bianco  (Etna)     White Blend   
1      Quinta dos Avidagos 2011 Avidagos Red (Douro)  Portuguese Red   
2      Rainstorm 2013 Pinot Gris (Willamette Valley)      Pinot Gris   
3  St. Julian 2013 Reserve Late Harvest Riesling ...        Riesling   
4  Sweet Cheeks 2012 Vintner's Reserve Wild Child...      Pinot Noir   

           winery_name  rating  price  
0              Nicosia      87    NaN  
1  Quinta dos Avidagos      87   15.0  
2            Rainstorm      87   14.0  
3           St. Julian      87   13.0  
4         Sweet Cheeks      87   65.0

In [61]:
# Drop any records that have emply values in any of their column fields
df_wine_base = df_wine_base.dropna(how='any')
print("Total records ", df_wine_base['wine_id'].count())
df_wine_base.head()

Total records  101400


wine_id   country_name      province_name          region_name  \
2        2  United States             Oregon    Willamette Valley   
3        3  United States           Michigan  Lake Michigan Shore   
4        4  United States             Oregon    Willamette Valley   
5        5          Spain     Northern Spain              Navarra   
6        6          Italy  Sicily & Sardinia             Vittoria   

                                           wine_name           wine_type  \
2      Rainstorm 2013 Pinot Gris (Willamette Valley)          Pinot Gris   
3  St. Julian 2013 Reserve Late Harvest Riesling ...            Riesling   
4  Sweet Cheeks 2012 Vintner's Reserve Wild Child...          Pinot Noir   
5  Tandem 2011 Ars In Vitro Tempranillo-Merlot (N...  Tempranillo-Merlot   
6   Terre di Giurfo 2013 Belsito Frappato (Vittoria)            Frappato   

       winery_name  rating  price  
2        Rainstorm      87   14.0  
3       St. Julian      87   13.0  
4     Sweet Cheeks      87   65.0  
5           Tandem      87   15.0  
6  Terre di Giurfo      87   16.0

In [62]:
# Group df_wine_base and calculate average price and rating per unique wine in the database)
df_wine_data = df_wine_base.groupby([ # 'wine_id' ,
                                     'country_name', 
                                     'province_name', 
                                     'region_name',
                                     'winery_name',
                                     'wine_type',
                                     'wine_name' 
                                     ], as_index=False)['rating','price'].mean().copy()

df_wine_data.reset_index(inplace=True)
print("Total records ", df_wine_data['country_name'].count())
df_wine_data.head()

Total records  92841


index country_name     province_name region_name winery_name  \
0      0    Argentina  Mendoza Province      Agrelo       Cadus   
1      1    Argentina  Mendoza Province      Agrelo    Casarena   
2      2    Argentina  Mendoza Province      Agrelo    Casarena   
3      3    Argentina  Mendoza Province      Agrelo    Casarena   
4      4    Argentina  Mendoza Province      Agrelo  El Enemigo   

            wine_type                                          wine_name  \
0  Cabernet Sauvignon             Cadus 2014 Cabernet Sauvignon (Agrelo)   
1  Cabernet Sauvignon  Casarena 2009 Estate Bottled Cabernet Sauvigno...   
2  Cabernet Sauvignon  Casarena 2012 Owen's Vineyard Cabernet Sauvign...   
3              Malbec    Casarena 2011 Lauren's Vineyard Malbec (Agrelo)   
4      Cabernet Franc  El Enemigo 2013 Gran Enemigo Agrelo Single Vin...   

   rating  price  
0    88.0   20.0  
1    84.0   17.0  
2    87.0   40.0  
3    89.0   40.0  
4    93.0  120.0

In [63]:
# DATASOURCE 2: extract country information from countries.csv - source: wikipedia
    
country_file = "Resources/countries.csv"
df_countries = pd.read_csv(country_file)
df_countries.head()
df_countries.reset_index(inplace=True)
df_countries = df_countries.rename(columns={'index':'country_id',
                                            'country':'country_abbr',
                                            'name': 'country_name'})
df_countries = df_countries.dropna(how='any')
print("Total records: ", df_countries['country_id'].count())
      
df_countries.head()

Total records:  243


country_id country_abbr   latitude  longitude          country_name
0           0           AD  42.546245   1.601554               Andorra
1           1           AE  23.424076  53.847818  United Arab Emirates
2           2           AF  33.939110  67.709953           Afghanistan
3           3           AG  17.060816 -61.796428   Antigua and Barbuda
4           4           AI  18.220554 -63.068615              Anguilla

In [64]:
# DATASOURCE 3: Directly load the temperatures by country table of the internet - source: Wikipedia
url = 'https://en.wikipedia.org/wiki/List_of_countries_by_average_yearly_temperature'
tables = pd.read_html(url)

df_temps = pd.DataFrame(tables[0])

# Rename columns
df_temps = df_temps.rename(columns={'Country':'country_name','Average yearly temperature (1961–1990, degrees Celsius)':'avg_temp'})

# Reset index for fast lookup by df_countries
df_temps = df_temps.set_index('country_name')

print("Total records: ", df_temps['avg_temp'].count())
df_temps.head()

Total records:  191


avg_temp
country_name         
Burkina Faso    28.25
Mali            28.25
Kiribati        28.20
Djibouti        28.00
Tuvalu          28.00

# STEP 2: TRANSFORM

In [65]:
# Add temperature to df_countries when found
df_countries['temperature'] = ""
list_temp = []

for index, row in df_countries.iterrows():
    try:
        list_temp = df_temps.loc[str(row[4]),'avg_temp']
        df_countries.iloc[index, 5] = list_temp
    except:
        pass

# Two dataframes - one for saving to the database later that includes the index_id and the other for lookup for df_wine_data
df_countries.head()
df_countries_lookup = df_countries.copy()
df_countries_lookup = df_countries_lookup.set_index("country_name")
df_countries_lookup.head()

country_id country_abbr   latitude  longitude  \
country_name                                                          
Andorra                        0           AD  42.546245   1.601554   
United Arab Emirates           1           AE  23.424076  53.847818   
Afghanistan                    2           AF  33.939110  67.709953   
Antigua and Barbuda            3           AG  17.060816 -61.796428   
Anguilla                       4           AI  18.220554 -63.068615   

                     temperature  
country_name                      
Andorra                    07.60  
United Arab Emirates       27.00  
Afghanistan                12.60  
Antigua and Barbuda        26.00  
Anguilla

In [66]:
# from df_wine_base, create seperate tables, to normalize the database
# df_wineries, df_provinces and df_regions. df_countries was created by pulling so called 'master data' of the internet.

# For the wineries

df_winery_base = df_wine_base.groupby(['winery_name']).count()
df_winery_base.reset_index(inplace=True)
df_wineries = df_winery_base[['winery_name']]
df_wineries.reset_index(inplace=True)
df_wineries = df_wineries.rename(columns={'index':'winery_id'})
print("Total records: ", df_wineries['winery_id'].count())

# Two dataframes - one for saving to the database later that includes the index_id and the other for lookup for df_wine_data
df_wineries.head()
df_wineries_lookup = df_wineries.copy()
df_wineries_lookup = df_wineries_lookup.set_index("winery_name")
df_wineries_lookup.head()

Total records:  13747


winery_id
winery_name                
1+1=3                     0
10 Knots                  1
100 Percent Wine          2
1000 Stories              3
1070 Green                4

In [67]:
# For the provinces

df_provinces_base = df_wine_base.groupby(['province_name']).count()
df_provinces_base.reset_index(inplace=True)
df_provinces = df_provinces_base[['province_name']]
df_provinces.reset_index(inplace=True)
df_provinces = df_provinces.rename(columns={'index':'province_id'})
print("Total records: ", df_provinces['province_id'].count())

# Two dataframes - one for saving to the database later that includes the index_id and the other for lookup for df_wine_data
df_provinces.head()
df_provinces_lookup = df_provinces.copy()
df_provinces_lookup = df_provinces_lookup.set_index("province_name")
df_provinces_lookup.head()

Total records:  65


province_id
province_name               
Alsace                     0
Andalucia                  1
Arizona                    2
Australia Other            3
Beaujolais                 4

In [68]:
# For the regions

df_regions_base = df_wine_base.groupby(['region_name']).count()
df_regions_base.reset_index(inplace=True)
df_regions = df_regions_base[['region_name']]
df_regions.reset_index(inplace=True)
df_regions = df_regions.rename(columns={'index':'region_id'})
print("Total records: ", df_regions['region_id'].count())

# Two dataframes - one for saving to the database later that includes the index_id and the other for lookup for df_wine_data
df_regions.head()
df_regions_lookup = df_regions.copy()
df_regions_lookup = df_regions_lookup.set_index("region_name")
df_regions_lookup.head()

Total records:  1204


region_id
region_name                 
Abruzzo                    0
Adelaida District          1
Adelaide                   2
Adelaide Hills             3
Adelaide Plains            4

In [69]:
# For the wine_types

df_wine_types_base = df_wine_base.groupby(['wine_type']).count()
df_wine_types_base.reset_index(inplace=True)
df_wine_types = df_wine_types_base[['wine_type']]
df_wine_types.reset_index(inplace=True)
df_wine_types = df_wine_types.rename(columns={'index':'wine_type_id'})
print("Total records: ", df_wine_types['wine_type_id'].count())

# Two dataframes - one for saving to the database later that includes the index_id and the other for lookup for df_wine_data
df_wine_types.head()
df_wine_types_lookup = df_wine_types.copy()
df_wine_types_lookup = df_wine_types_lookup.set_index("wine_type")
df_wine_types_lookup.head()

Total records:  509


wine_type_id
wine_type              
Abouriou              0
Aglianico             1
Airen                 2
Albana                3
Albanello             4

In [70]:
# For reference for the part below: df_wine_base before
df_wine_data.head()

index country_name     province_name region_name winery_name  \
0      0    Argentina  Mendoza Province      Agrelo       Cadus   
1      1    Argentina  Mendoza Province      Agrelo    Casarena   
2      2    Argentina  Mendoza Province      Agrelo    Casarena   
3      3    Argentina  Mendoza Province      Agrelo    Casarena   
4      4    Argentina  Mendoza Province      Agrelo  El Enemigo   

            wine_type                                          wine_name  \
0  Cabernet Sauvignon             Cadus 2014 Cabernet Sauvignon (Agrelo)   
1  Cabernet Sauvignon  Casarena 2009 Estate Bottled Cabernet Sauvigno...   
2  Cabernet Sauvignon  Casarena 2012 Owen's Vineyard Cabernet Sauvign...   
3              Malbec    Casarena 2011 Lauren's Vineyard Malbec (Agrelo)   
4      Cabernet Franc  El Enemigo 2013 Gran Enemigo Agrelo Single Vin...   

   rating  price  
0    88.0   20.0  
1    84.0   17.0  
2    87.0   40.0  
3    89.0   40.0  
4    93.0  120.0

In [73]:
# Now replace all _name strings in df_wine_base with their correlating _id keys
print("Start time: ", datetime.datetime.now().time())
# limit = 3

for index, row in df_wine_data.iterrows():
    try:
        country_id = df_countries_lookup.loc[str(row[1]),'country_id']
        df_wine_data.loc[index, 'country_name'] = country_id
        print(country_id)
        province_id = df_provinces_lookup.loc[str(row[2]),'province_id']
        df_wine_data.loc[index, 'province_name'] = province_id
        print(province_id)
        region_id = df_regions_lookup.loc[str(row[3]),'region_id']
        df_wine_data.loc[index, 'region_name'] = region_id
        print(region_id)
        winery_id = df_wineries_lookup.loc[str(row[4]),'winery_id']
        df_wine_data.loc[index, 'winery_name'] = winery_id
        print(winery_id)
        wine_type_id = df_wine_types_lookup.loc[str(row[5]),'wine_type_id']
        df_wine_data.loc[index, 'wine_type'] = wine_type_id
        print(wine_type_id)
    except:
        pass
#     if index == limit:
#             break
    
print("Finish time: ", datetime.datetime.now().time())

Start time:  15:47:23.848662
10
29
9
5785
41
10
29
9
6226
34
10
29
9
6226
48
10
29
9
6226
48
10
29
9
6226
198
10
29
9
6226
300
10
29
9
6226
342
10
29
9
6226
342
10
29
9
8090
33
10
29
9
8090
33
10
29
9
8090
33
10
29
9
8090
33
10
29
9
8090
33
10
29
9
8090
33
10
29
9
8090
33
10
29
9
8090
41
10
29
9
8090
41
10
29
9
8090
41
10
29
9
8090
41
10
29
9
8090
48
10
29
9
8090
48
10
29
9
8090
48
10
29
9
8090
48
10
29
9
8090
48
10
29
9
8090
48
10
29
9
8090
48
10
29
9
8090
198
10
29
9
8090
198
10
29
9
8090
198
10
29
9
8090
198
10
29
9
8090
198
10
29
9
8090
198
10
29
9
8090
198
10
29
9
8090
198
10
29
9
8090
198
10
29
9
8090
198
10
29
9
8090
198
10
29
9
8090
198
10
29
9
8090
198
10
29
9
8792
87
10
29
9
8792
198
10
29
9
8964
198
10
29
9
11483
87
10
29
9
12649
34
10
29
29
8575
198
10
29
525
112
198
10
29
525
332
48
10
29
525
332
48
10
29
525
332
198
10
29
525
332
198
10
29
525
332
198
10
29
525
332
198
10
29
525
332
198
10
29
525
332
198
10
29
525
332
198
10
29
525
332
198
10
29
525
332
198
10
29
525
332


10
29
622
972
404
10
29
622
1086
198
10
29
622
1086
198
10
29
622
1086
198
10
29
622
1087
48
10
29
622
1087
87
10
29
622
1087
198
10
29
622
1157
198
10
29
622
1158
198
10
29
622
1158
425
10
29
622
1160
48
10
29
622
1160
48
10
29
622
1160
198
10
29
622
1160
198
10
29
622
1160
198
10
29
622
1160
198
10
29
622
1160
198
10
29
622
1160
322
10
29
622
1160
419
10
29
622
1160
419
10
29
622
1160
419
10
29
622
1160
419
10
29
622
1161
48
10
29
622
1161
48
10
29
622
1161
48
10
29
622
1161
48
10
29
622
1161
48
10
29
622
1161
48
10
29
622
1161
48
10
29
622
1161
52
10
29
622
1161
52
10
29
622
1161
87
10
29
622
1161
87
10
29
622
1161
87
10
29
622
1161
87
10
29
622
1161
87
10
29
622
1161
87
10
29
622
1161
87
10
29
622
1161
87
10
29
622
1161
87
10
29
622
1161
87
10
29
622
1161
87
10
29
622
1161
87
10
29
622
1161
198
10
29
622
1161
198
10
29
622
1161
198
10
29
622
1161
198
10
29
622
1161
198
10
29
622
1161
198
10
29
622
1161
198
10
29
622
1161
198
10
29
622
1161
198
10
29
622
1161
198
10
29
622
1161
198


29
622
5697
33
10
29
622
5697
33
10
29
622
5697
33
10
29
622
5697
33
10
29
622
5697
33
10
29
622
5697
41
10
29
622
5697
41
10
29
622
5697
41
10
29
622
5697
48
10
29
622
5697
48
10
29
622
5697
198
10
29
622
5697
198
10
29
622
5697
198
10
29
622
5697
198
10
29
622
5697
198
10
29
622
5697
198
10
29
622
5697
198
10
29
622
5697
342
10
29
622
5697
342
10
29
622
5697
342
10
29
622
5697
342
10
29
622
5697
342
10
29
622
5784
342
10
29
622
5785
33
10
29
622
5785
33
10
29
622
5785
33
10
29
622
5785
34
10
29
622
5785
41
10
29
622
5785
41
10
29
622
5785
41
10
29
622
5785
41
10
29
622
5785
41
10
29
622
5785
41
10
29
622
5785
41
10
29
622
5785
41
10
29
622
5785
41
10
29
622
5785
41
10
29
622
5785
41
10
29
622
5785
42
10
29
622
5785
44
10
29
622
5785
87
10
29
622
5785
87
10
29
622
5785
87
10
29
622
5785
87
10
29
622
5785
87
10
29
622
5785
198
10
29
622
5785
198
10
29
622
5785
198
10
29
622
5785
342
10
29
622
5788
48
10
29
622
5788
425
10
29
622
5788
451
10
29
622
5790
198
10
29
622
5807
48
10
29
622
5

29
622
8603
40
10
29
622
8603
44
10
29
622
8603
44
10
29
622
8603
48
10
29
622
8603
87
10
29
622
8603
198
10
29
622
8603
199
10
29
622
8603
322
10
29
622
8603
322
10
29
622
8603
342
10
29
622
8603
342
10
29
622
8603
425
10
29
622
8603
502
10
29
622
8611
48
10
29
622
8611
48
10
29
622
8611
87
10
29
622
8611
198
10
29
622
8611
198
10
29
622
8611
198
10
29
622
8611
198
10
29
622
8611
198
10
29
622
8622
198
10
29
622
8622
198
10
29
622
8664
198
10
29
622
8664
198
10
29
622
8664
198
10
29
622
8664
198
10
29
622
8721
33
10
29
622
8721
33
10
29
622
8721
48
10
29
622
8721
48
10
29
622
8721
198
10
29
622
8721
198
10
29
622
8721
198
10
29
622
8721
198
10
29
622
8721
354
10
29
622
8721
371
10
29
622
8792
198
10
29
622
8792
198
10
29
622
8792
198
10
29
622
8792
198
10
29
622
8792
198
10
29
622
8792
198
10
29
622
8809
198
10
29
622
8809
371
10
29
622
8858
87
10
29
622
8858
198
10
29
622
8858
354
10
29
622
8860
87
10
29
622
8868
198
10
29
622
8973
198
10
29
622
9012
34
10
29
622
9012
34
10
29
622
90

10
29
622
12120
48
10
29
622
12120
87
10
29
622
12120
87
10
29
622
12120
87
10
29
622
12120
87
10
29
622
12120
87
10
29
622
12120
198
10
29
622
12120
198
10
29
622
12120
198
10
29
622
12120
198
10
29
622
12120
198
10
29
622
12120
198
10
29
622
12120
198
10
29
622
12120
198
10
29
622
12120
232
10
29
622
12120
232
10
29
622
12120
322
10
29
622
12120
342
10
29
622
12120
342
10
29
622
12120
354
10
29
622
12120
354
10
29
622
12120
451
10
29
622
12143
198
10
29
622
12143
198
10
29
622
12143
203
10
29
622
12143
342
10
29
622
12152
87
10
29
622
12152
198
10
29
622
12152
198
10
29
622
12152
232
10
29
622
12158
198
10
29
622
12158
425
10
29
622
12320
33
10
29
622
12320
198
10
29
622
12320
198
10
29
622
12320
198
10
29
622
12320
198
10
29
622
12320
198
10
29
622
12320
198
10
29
622
12320
364
10
29
622
12320
451
10
29
622
12320
451
10
29
622
12352
48
10
29
622
12352
48
10
29
622
12352
48
10
29
622
12352
48
10
29
622
12352
48
10
29
622
12352
48
10
29
622
12352
87
10
29
622
12352
87
10
29
622
12352


...

1187
10855
342
226
63
1187
10855
342
226
63
1187
10855
404
226
63
1187
10855
404
226
63
1187
10855
404
226
63
1187
10855
404
226
63
1187
10855
404
226
63
1187
10855
404
226
63
1187
10855
404
226
63
1187
10855
419
226
63
1187
10855
419
226
63
1187
10913
48
226
63
1187
10913
48
226
63
1187
10913
48
226
63
1187
10913
404
226
63
1187
10913
404
226
63
1187
10913
404
226
63
1187
10913
404
226
63
1187
10913
404
226
63
1187
10913
404
226
63
1187
10913
404
226
63
1187
10913
404
226
63
1187
10913
404
226
63
1187
10913
404
226
63
1187
10913
404
226
63
1187
10913
404
226
63
1187
10913
404
226
63
1187
10913
404
226
63
1187
10913
404
226
63
1187
10913
404
226
63
1187
10913
502
226
63
1187
10948
198
226
63
1187
10948
364
226
63
1187
10948
425
226
63
1187
11167
87
226
63
1187
11167
342
226
63
1187
11193
344
226
63
1187
11193
345
226
63
1187
11193
345
226
63
1187
11193
404
226
63
1187
11347
48
226
63
1187
11347
404
226
63
1187
11366
404
226
63
1187
11371
34
226
63
1187
11371
34
226
63
1187
11371
34
226

87
226
63
1188
761
87
226
63
1188
814
21
226
63
1188
814
404
226
63
1188
1030
322
226
63
1188
1030
322
226
63
1188
1045
316
226
63
1188
1146
342
226
63
1188
1367
87
226
63
1188
1368
48
226
63
1188
1368
48
226
63
1188
1368
87
226
63
1188
1368
87
226
63
1188
1368
232
226
63
1188
1368
318
226
63
1188
1368
318
226
63
1188
1368
318
226
63
1188
1368
318
226
63
1188
1368
404
226
63
1188
1368
404
226
63
1188
1368
404
226
63
1188
1368
404
226
63
1188
1417
48
226
63
1188
1417
48
226
63
1188
1417
48
226
63
1188
1417
48
226
63
1188
1417
48
226
63
1188
1417
87
226
63
1188
1417
232
226
63
1188
1417
232
226
63
1188
1417
232
226
63
1188
1417
342
226
63
1188
1582
87
226
63
1188
1582
87
226
63
1188
1582
316
226
63
1188
1658
344
226
63
1188
1694
41
226
63
1188
1694
41
226
63
1188
1694
41
226
63
1188
1694
48
226
63
1188
1694
48
226
63
1188
1694
48
226
63
1188
1694
232
226
63
1188
1694
342
226
63
1188
1694
342
226
63
1188
1762
149
226
63
1188
2311
342
226
63
1188
2358
347
226
63
1188
2373
48
226
63
1188
23

342
226
63
1195
197
342
226
63
1195
197
342
226
63
1195
197
342
226
63
1195
197
342
226
63
1195
197
344
226
63
1195
197
344
226
63
1195
197
344
226
63
1195
197
345
226
63
1195
197
345
226
63
1195
197
347
226
63
1195
197
347
226
63
1195
197
347
226
63
1195
197
347
226
63
1195
197
354
226
63
1195
197
354
226
63
1195
197
354
226
63
1195
197
354
226
63
1195
197
371
226
63
1195
197
371
226
63
1195
197
371
226
63
1195
197
371
226
63
1195
197
371
226
63
1195
197
371
226
63
1195
197
404
226
63
1195
197
404
226
63
1195
197
419
226
63
1195
197
425
226
63
1195
197
491
226
63
1195
197
491
226
63
1195
197
502
226
63
1195
197
502
226
63
1195
197
507
226
63
1195
296
232
226
63
1195
296
404
226
63
1195
370
371
226
63
1195
430
34
226
63
1195
430
34
226
63
1195
430
34
226
63
1195
430
34
226
63
1195
430
342
226
63
1195
430
342
226
63
1195
430
364
226
63
1195
460
41
226
63
1195
460
41
226
63
1195
460
301
226
63
1195
460
301
226
63
1195
460
301
226
63
1195
460
301
226
63
1195
460
404
226
63
1195
460
425
22

63
1195
7754
344
226
63
1195
7754
344
226
63
1195
7754
404
226
63
1195
7754
404
226
63
1195
7754
404
226
63
1195
7754
410
226
63
1195
7776
48
226
63
1195
7776
97
226
63
1195
7776
263
226
63
1195
7776
504
226
63
1195
7804
404
226
63
1195
8149
318
226
63
1195
8452
19
226
63
1195
8452
34
226
63
1195
8452
97
226
63
1195
8452
404
226
63
1195
8458
410
226
63
1195
8458
419
226
63
1195
8478
34
226
63
1195
8478
48
226
63
1195
8478
48
226
63
1195
8478
87
226
63
1195
8478
87
226
63
1195
8478
87
226
63
1195
8478
87
226
63
1195
8478
149
226
63
1195
8478
318
226
63
1195
8478
318
226
63
1195
8478
318
226
63
1195
8478
342
226
63
1195
8478
342
226
63
1195
8478
342
226
63
1195
8478
347
226
63
1195
8478
347
226
63
1195
8478
354
226
63
1195
8478
404
226
63
1195
8478
404
226
63
1195
8727
87
226
63
1195
8727
87
226
63
1195
8727
159
226
63
1195
8727
159
226
63
1195
8727
159
226
63
1195
8727
220
226
63
1195
8727
220
226
63
1195
8727
344
226
63
1195
8727
355
226
63
1195
8727
404
226
63
1195
8727
404
226
63
119

1195
12779
48
226
63
1195
12779
48
226
63
1195
12779
48
226
63
1195
12779
232
226
63
1195
12779
232
226
63
1195
12779
342
226
63
1195
12779
404
226
63
1195
12779
404
226
63
1195
12784
101
226
63
1195
12784
101
226
63
1195
12784
149
226
63
1195
12784
159
226
63
1195
12784
160
226
63
1195
12784
160
226
63
1195
12784
160
226
63
1195
12784
160
226
63
1195
12784
160
226
63
1195
12784
355
226
63
1195
12822
149
226
63
1195
12846
48
226
63
1195
12846
87
226
63
1195
12846
404
226
63
1195
12846
404
226
63
1195
13376
342
226
63
1195
13386
258
226
63
1195
13400
491
226
63
1195
13454
364
226
63
1195
13507
404
226
63
1195
13507
404
226
63
1195
13507
404
226
63
1195
13507
404
226
63
1195
13507
491
226
63
1195
13522
26
226
63
1195
13522
41
226
63
1195
13522
318
226
63
1195
13522
318
226
63
1195
13522
318
226
63
1195
13522
318
226
63
1195
13522
318
226
63
1195
13522
347
226
63
1195
13522
347
226
63
1195
13522
371
226
63
1195
13522
404
226
63
1195
13525
34
226
63
1195
13525
87
226
63
1195
13525
159
226


In [74]:
df_wine_data.head()

index  country_name  province_name  region_name  winery_name  wine_type  \
0      0            10             29            9         1650         48   
1      1            10             29            9         2020         48   
2      2            10             29            9         2020         48   
3      3            10             29            9         2020        198   
4      4            10             29            9         5785         41   

                                           wine_name  rating  price  
0             Cadus 2014 Cabernet Sauvignon (Agrelo)    88.0   20.0  
1  Casarena 2009 Estate Bottled Cabernet Sauvigno...    84.0   17.0  
2  Casarena 2012 Owen's Vineyard Cabernet Sauvign...    87.0   40.0  
3    Casarena 2011 Lauren's Vineyard Malbec (Agrelo)    89.0   40.0  
4  El Enemigo 2013 Gran Enemigo Agrelo Single Vin...    93.0  120.0

In [77]:
df_wine_data = df_wine_data.rename(columns={'index':'wine_id',
                                            'country_name':'country_id',
                                            'province_name':'province_id',
                                            'region_name':'region_id',
                                            'wine_type':'wine_type_id',
                                            'winery_name':'winery_id'})
df_wine_data.head()

wine_id  country_id  province_id  region_id  winery_id  wine_type_id  \
0        0          10           29          9       1650            48   
1        1          10           29          9       2020            48   
2        2          10           29          9       2020            48   
3        3          10           29          9       2020           198   
4        4          10           29          9       5785            41   

                                           wine_name  rating  price  
0             Cadus 2014 Cabernet Sauvignon (Agrelo)    88.0   20.0  
1  Casarena 2009 Estate Bottled Cabernet Sauvigno...    84.0   17.0  
2  Casarena 2012 Owen's Vineyard Cabernet Sauvign...    87.0   40.0  
3    Casarena 2011 Lauren's Vineyard Malbec (Agrelo)    89.0   40.0  
4  El Enemigo 2013 Gran Enemigo Agrelo Single Vin...    93.0  120.0

# STEP 3: LOAD

In [80]:
# Create connection
connection_string = "postgres:postgres@localhost:5432/wine_db"
engine = create_engine(f'postgresql://{connection_string}')

In [82]:
# Load all 5 dataframes into their respective tables
df_countries.to_sql(name='countries', con=engine, if_exists='replace', index=False)
# df_provinces.to_sql(name='provinces', con=engine, if_exists='replace', index=False)
# df_regions.to_sql(name='regions', con=engine, if_exists='replace', index=False)
# df_wineries.to_sql(name='wineries', con=engine, if_exists='replace', index=False)
# df_wine_base.to_sql(name='wines', con=engine, if_exists='replace', index=False)

OperationalError: (psycopg2.OperationalError) FATAL:  password authentication failed for user "postgres"

(Background on this error at: http://sqlalche.me/e/e3q8)

In [ ]:
# Create one sql statement, that shows all data is now connected